In [1]:
!pip install open3d

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 420.5/420.5 MB 2.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.3/10.3 MB 72.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.1/77.1 kB 9.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 138.3/138.3 kB 16.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 95.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.6/233.6 kB 25.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 65.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 80.3 MB/s eta 0:00:00
  Attempting uninstall: widgetsnbextension
    Found existing installation: widgetsnbextension 3.6.4
    Uninstalling widgetsnbextension-3.6.4:
      Successfully uninstalled widgetsnbextension-3.6.4
  Attempting uninstall: werkzeug
    Found existing installa

**Import Packages**

In [2]:
import open3d as o3d
import cv2
import numpy as np

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


**Define Object Fraame**

In [4]:
object_frame_translation = np.array([1.0, 2.0, 3.0])  # Translation vector
object_frame_rotation = np.eye(3)  # Rotation matrix
transformation = np.eye(4)
transformation[:3, :3] = object_frame_rotation
transformation[:3, 3] = object_frame_translation
print("Object Frame:",transformation)

Object Frame: [[1. 0. 0. 1.]
 [0. 1. 0. 2.]
 [0. 0. 1. 3.]
 [0. 0. 0. 1.]]


**ICP Algorithm**

In [5]:
# Load point clouds
source_cloud11 = o3d.io.read_point_cloud("/content/drive/MyDrive/6 DoF Pose Estimation/cereal_box_1/separated/cereal_box_1_1_1_separated.pcd")
target_cloud11 = o3d.io.read_point_cloud("/content/drive/MyDrive/6 DoF Pose Estimation/cereal_box_1/separated/cereal_box_1_1_2_separated.pcd")


# ICP registration
icp_transformation = o3d.pipelines.registration.registration_icp(
    source_cloud11, target_cloud11, max_correspondence_distance=0.05,
    criteria=o3d.pipelines.registration.ICPConvergenceCriteria(max_iteration=200)
)

# Create a new transformation matrix 
transformation = np.eye(4)
transformation[:3, :3] = object_frame_rotation
transformation[:3, 3] = object_frame_translation

transformation_matrix1 = icp_transformation.transformation


# Apply the transformation to the source cloud
registered_cloud11 = source_cloud11.transform(icp_transformation.transformation@ transformation)


# Visualize the registered result
o3d.visualization.draw_plotly([ registered_cloud11,target_cloud11])
print("Transformation_Matrix;",transformation_matrix1)

Transformation_Matrix; [[ 0.97607986  0.17792347 -0.12494539  0.20590451]
 [-0.18197612  0.98306314 -0.02171523 -0.02189178]
 [ 0.11896556  0.04393288  0.99192595  0.01084753]
 [ 0.          0.          0.          1.        ]]


In [6]:
source_cloud12=registered_cloud11
target_cloud12 = o3d.io.read_point_cloud("/content/drive/MyDrive/6 DoF Pose Estimation/cereal_box_1/separated/cereal_box_1_1_3_separated.pcd")


icp_transformation = o3d.pipelines.registration.registration_icp(
    source_cloud12, target_cloud12, max_correspondence_distance=0.05,
    criteria=o3d.pipelines.registration.ICPConvergenceCriteria(max_iteration=200)
)


transformation = np.eye(4)
transformation[:3, :3] = object_frame_rotation
transformation[:3, 3] = object_frame_translation

transformation_matrix2 = icp_transformation.transformation

registered_cloud12 = target_cloud12.transform(icp_transformation.transformation@ transformation)

o3d.visualization.draw_plotly([registered_cloud12])
print("Transformation_Matrix;",transformation_matrix2)

Transformation_Matrix; [[1. 0. 0. 0.]
 [0. 1. 0. 0.]
 [0. 0. 1. 0.]
 [0. 0. 0. 1.]]


**IN OUR ORIGINAL IPYNB FILE WE HAD DONE THIS KIND OF REGISTRATION FOR ALL OBJECTS VIEWS AND POSES BUT UNABLEE TO OBTAIN A BETTER RESULT DUE TO KEYPOINT MATCHING**